<a href="https://colab.research.google.com/github/nickolasnolte1/Dividers/blob/master/BigM.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import numpy as np
from sympy import symbols, Eq
from tabulate import tabulate

In [ ]:
# Se inicializa M como una variable
M = symbols('M')

In [ ]:
def getMin(arr): 
  '''
    Esta función busca el valor mínimo 
  '''
  lastLine = list(arr[-1])
  lastLine.pop()
  print(lastLine)
  min = 0
  expr = 0
  for val in lastLine:
    if M in val.free_symbols:
      result = val.subs(M, 1000)
      if result < min:
        min = result
        expr = val
    else:
      if val < min:
        min = val
        expr = min
  return min, lastLine.index(expr)

def getMax(arr):
  lastLine = list(arr[-1])
  lastLine.pop()
  lastLine.pop()
  max = 0
  expr = 0
  for val in lastLine:
    if M in val.free_symbols:
      result = val.subs(M, 1000)
      if result > max:
        max = result
        expr = val
    else:
      if val > max:
        max = val
        expr = max
  return max, lastLine.index(expr)


def getPositiveMin(arr):
  ogArr = [] 
  for val in arr:
    ogArr.append(val)
  for val in ogArr:
    if val < 0:
      arr.remove(val)
  
  arr = np.array(arr)
  minVal = np.amin(arr)
  return minVal, ogArr

def replaceM(arr):
  lastRow = arr[-1]
  for x in range(len(lastRow)):
    if isinstance(lastRow[x], int) or isinstance(lastRow[x], float):
      continue
    else:
      newVal = lastRow[x].subs(M, 1000)
      lastRow[x] = newVal
  
  arr[-1] = lastRow
  return arr

In [ ]:
# Se ingresa el numero de restricciones que tendra el problema
numConstraints = int(input("Ingrese el numero de restricciones que desee: "))
numVars = int(input("Ingrese el numero de variables que contendra cada restriccion que desee: "))
choice = input("Si es un problema de minimizacion ingrese 'MIN' y si es un problema de maximizacion ingres 'MAX': ")

choice = choice.upper()

# Se inicializa la lista de restricciones
rest = []
# Se inicializa la lista en donde estaran las desigualdades
inequalities = []
# Se inicializa la lista de los recursos disponibles
recur = []
contador = 0
for cons in range (0, numConstraints):
  contador += 1
  c = []

  # Se ingresan las variables de cada restriccion
  print(f"Ingrese las variables de su restriccion numero {contador}: ")
  for vars in range(0, numVars):
    var = float(input())
    c.append(var)
  rest.append(c)
  print("Para ingresar desigualdades ingrese los siguientes numeros:\n'<=' = 1\n'>=' = 2\n'=' = 3\n")
  symbol = int(input(f'Ingrese la desigualdad de su restriccion numero {contador}: '))
  inequalities.append(symbol)

  # Se ingresa la cantidad disponible de los recursos
  var = int(input(f"Ahora ingrese el recurso disponible de la restriccion numero {contador}: "))
  recur.append(var)

#Se inicializa la lista de coeficientes
coef = []
# Se ingresan los coeficientes de la funcion objetivo
print("Por ultimo, ingrese los coeficientes de su funcion objetivo: ")
for vars in range(0, numVars):
  var = int(input())
  coef.append(var)

In [ ]:
''' En este paso se va a verificar si alguno de los recursos disponibles
de las restricciones es negativo, en caso si sea negativo se multiplica 
por -1 en ambos lados '''

# rest = [[3, 1], [4, 3], [1, 2]]
# coef = [4, 1]
# recur = [3, 6, 4]
# inequalities = [3, 2, 1]

# numVars = 2
# numConstraints = 3

# choice = 'MIN'

for i in range(len(recur)):
  if recur[i] < 0: 
    recur[i] = recur[i]*-1
    if inequalities[i] == 1:
      inequalities[i] = 2
    elif inequalities[i] == 2:
      inequalities[i] = 1
    for x in range(len(rest[i])):
      rest[i][x] = rest[i][x] * -1

print(f"Restricciones: {rest}")
print(f"Recursos disponibles: {recur}")
print(f"Funcion objetivo: {coef}")

In [ ]:
''' En este paso se agregaran todas las variables slack y aritificiales'''

slackVars = 0
artVars = 0

'''Calcula cuantas variables slack y artificales existen en el problema 
tomando en cuenta las desigualdades de las restricciones '''
for x in inequalities:
  if x == 1:
    slackVars =  slackVars + 1
  elif x == 2:
    slackVars = slackVars + 1
    artVars = artVars + 1
  elif x == 3:
    artVars = artVars + 1

print(f"Variables slack: {slackVars}")
print(f"Variables artificiales: {artVars}")
totalExtraVars = slackVars + artVars

headers = []
for x in range(numVars):
  headers.append(f'X{x}')

for x in range(slackVars):
  headers.append(f'S{x}')

for x in range(artVars):
  headers.append(f'A{x}')

headers.append('P')
headers.append('P')

for el in range(len(rest)):
  for x in range(0, totalExtraVars + 1):
    rest[el].append(0)

s = numVars

slackIndex = numVars
restIndex = 0

for x in range(0, len(inequalities)):
  if inequalities[x] == 1:
    rest[x][slackIndex] = 1
    slackIndex = slackIndex + 1
  elif inequalities[x] == 2:
    rest[x][slackIndex] = -1
    slackIndex = slackIndex + 1

indexArt = numVars + slackVars

for x in range(0, len(inequalities)):
  if inequalities[x] == 2:
    rest[x][indexArt] = 1
    indexArt = indexArt + 1
  elif inequalities[x] == 3: 
    rest[x][indexArt] = 1
    indexArt = indexArt + 1

for el in range(0, len(rest)):
  rest[el].append(recur[el])

for x in range(len(coef)):
  coef[x] = coef[x] * -1

for vars in range(0, slackVars):
  coef.append(0)

if choice == 'MAX':
  for vars in range(0, artVars):
    coef.append(M)
elif choice == 'MIN':
  for vars in range(0, artVars):
    coef.append(-M)

coef.append(1)
coef.append(0)

# Se inicializa la tabla
table = []

# Este for recorre cada restriccion en la lista de todas las resticiones y las inserta en la tabla
for x in rest:
  table.append(x)

# Se inserta la lista de coeficientes en la tabla
table.append(coef)

# Convierto la tabla en un array de la libreria de numpy tipo float
table = np.array(table)

In [ ]:
print(tabulate(table, headers, tablefmt="fancy_grid"))

In [ ]:
'''Eliminacion de las Ms en las variables artificiales'''

lastRow = table[-1]
if choice == "MAX":
  print('MAXIMIZACION')
  if M in lastRow:
    M_index = np.where(lastRow == M)

elif choice == "MIN":
  print('MINIMZACION')
  if -M in lastRow:
    M_index = np.where(lastRow == -M)

M_index = list(M_index[0])

for x in M_index:
  one_col = table[:, x]
  if 1 in one_col:
    one_loc = np.where(one_col == 1)
    one_loc = int(one_loc[0])
    if lastRow[x] == M:
      row = table[one_loc]
      for i in range(len(row)):
        newVal = -M * row[i] + lastRow[i]
        table[-1][i] = newVal
    elif lastRow[x] == -M:
        row = table[one_loc]
        for i in range(len(row)):
          newVal = M * row[i] + lastRow[i]
          table[-1][i] = newVal


print(tabulate(table, headers, tablefmt="fancy_grid")) 

In [ ]:
''' Verifica que las basic variables todas sean positivas pq si hay negativas
significa que no existe solucion para el problema'''

basic_vars = list(table[:, -1])
basic_vars.pop()
for x in basic_vars:
  if x < 0:
    print('NO HAY SOLUCION') 

In [ ]:
noSol = True

if choice == 'MAX':
  while (noSol == True):
    print(tabulate(table, headers, tablefmt="fancy_grid"))
    
    # Utiliza la funcion getMin()
    # Esta retorna el valor mas pequeño en la ultima fila de la tabla y su posicion
    minNegative, location = getMin(table)
    # verifica que el minimo sea menor a cero, si no es se termina el while pues ya se tiene la tabla con los resultados
    if minNegative >= 1:
      noSol = False
      break
    
    # Utulizando la posicion del minimo se seleccion la columna pivote
    pivotColumn = table[:, location]
    # Se selecciona la ultima columna de la tabla 
    lastCol = table[:, -1]
    values = []
    # Se recorre este for el numero de restricciones que existen y
    # se divide cada valor de la ultima columna por cada valor de la columna pivote y se guarda en un arreglo
    for x in range (0, numConstraints):
      if pivotColumn[x] != 0:
        val = lastCol[x]/pivotColumn[x]
        values.append(val)
      else: 
        values.append(-1)
    # Devuelve el valor mas pequeño de la lista de respuestas
    min, ogVals = getPositiveMin(values)
    # Devuelve la posicion en donde se encuentra el minimo para luego utilizarlo para encontrar el pivot
    pivLoc = ogVals.index(min)
    pivot = pivotColumn[pivLoc]

    print(f"\nEl numero pivote es: {pivot}")

    # Con la misma posicion de antes vamos a traer la fila pivote
    pivotRow = np.array(table[pivLoc])
    # Se recorre la fila pivote y se divide cada valor por el pivote
    for i in range(len(pivotRow)):
      val = pivotRow[i]/pivot
      pivotRow[i] = val
    # Se remplaza la fila pivote modificada en la tabla
    table[pivLoc] = pivotRow
    printTable(table)
    numRows = len(table)
    
    # Se recorre cada fila
    for x in range(0, numRows):
      # Si la posicion del pivote es igual a la posicion que toca en la iteracion y se salta la fila
      if pivLoc == x:
        continue
      else:
        # Se trae la fila que se va a modifica
        row = np.array(table[x])
        # Es el coeficiente que va a afectar los valores de la fila pivote
        coef = pivotColumn[x]
        # Este for recorre los elementos de la fila que se esta modificando
        for i in range(len(row)):
          # Se hace la operacion con el coeficiente a cada elemento de la fila
          # para hacer cero los valores arriba del pivote
          newVal = row[i] - coef*pivotRow[i]
          row[i] = newVal
        # Se inserta la fila modificada en la tabla
        table[x] = row

    print("TABLA FINAL DE RESULTADOS")
    print(tabulate(table, headers, tablefmt="fancy_grid"))

Streaming output truncated to the last 5000 lines.
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    4 │    0 │    0 │ 1.0*M │   1 │ 900 │
╘══════╧══════╧══════╧══════╧══════╧══════╧═══════╧═════╧═════╛
[1.00000000000000, 0, 0, 4.00000000000000, 0, 0, 1.0*M, 1]

El numero pivote es: 1.0
TABLA FINAL DE RESULTADOS
╒══════╤══════╤══════╤══════╤══════╤══════╤═══════╤═════╤═════╕
│   X0 │   X1 │   S0 │   S1 │   S2 │   S3 │ A0    │   P │   P │
╞══════╪══════╪══════╪══════╪══════╪══════╪═══════╪═════╪═════╡
│    1 │    0 │    1 │   -1 │    0 │    0 │ 0.0   │   0 │ 375 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    2 │    0 │    1 │ -1.0  │   0 │ 300 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │   -4 │    1 │    0 │ 0.0   │   0 │ 100 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    1 │    0 │    1 │    0 │    0 │ 0.0   │   0 │ 225 │
├─────

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    4 │    0 │    0 │ 1.0*M │   1 │ 900 │
╘══════╧══════╧══════╧══════╧══════╧══════╧═══════╧═════╧═════╛
╒══════╤══════╤══════╤══════╤══════╤══════╤═══════╤═════╤═════╕
│   X0 │   X1 │   S0 │   S1 │   S2 │   S3 │ A0    │   P │   P │
╞══════╪══════╪══════╪══════╪══════╪══════╪═══════╪═════╪═════╡
│    1 │    0 │    1 │   -1 │    0 │    0 │ 0.0   │   0 │ 375 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    2 │    0 │    1 │ -1.0  │   0 │ 300 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │   -4 │    1 │    0 │ 0.0   │   0 │ 100 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    1 │    0 │    1 │    0 │    0 │ 0.0   │   0 │ 225 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    4 │    0 │    0 │ 1.0*M │  

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    4 │    0 │    0 │ 1.0*M │   1 │ 900 │
╘══════╧══════╧══════╧══════╧══════╧══════╧═══════╧═════╧═════╛
[1.00000000000000, 0, 0, 4.00000000000000, 0, 0, 1.0*M, 1]

El numero pivote es: 1.0
TABLA FINAL DE RESULTADOS
╒══════╤══════╤══════╤══════╤══════╤══════╤═══════╤═════╤═════╕
│   X0 │   X1 │   S0 │   S1 │   S2 │   S3 │ A0    │   P │   P │
╞══════╪══════╪══════╪══════╪══════╪══════╪═══════╪═════╪═════╡
│    1 │    0 │    1 │   -1 │    0 │    0 │ 0.0   │   0 │ 375 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    2 │    0 │    1 │ -1.0  │   0 │ 300 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │   -4 │    1 │    0 │ 0.0   │   0 │ 100 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    1 │    0 │    1 │    0 │    0 │ 0.0   │   0 │ 225 │
├─────

...

Streaming output truncated to the last 5000 lines.
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │   -4 │    1 │    0 │ 0.0   │   0 │ 100 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    1 │    0 │    1 │    0 │    0 │ 0.0   │   0 │ 225 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    4 │    0 │    0 │ 1.0*M │   1 │ 900 │
╘══════╧══════╧══════╧══════╧══════╧══════╧═══════╧═════╧═════╛
╒══════╤══════╤══════╤══════╤══════╤══════╤═══════╤═════╤═════╕
│   X0 │   X1 │   S0 │   S1 │   S2 │   S3 │ A0    │   P │   P │
╞══════╪══════╪══════╪══════╪══════╪══════╪═══════╪═════╪═════╡
│    1 │    0 │    1 │   -1 │    0 │    0 │ 0.0   │   0 │ 375 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    2 │    0 │    1 │ -1.0  │   0 │ 300 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │   -4 │    1 │    0 │ 0.0   │  

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    4 │    0 │    0 │ 1.0*M │   1 │ 900 │
╘══════╧══════╧══════╧══════╧══════╧══════╧═══════╧═════╧═════╛
╒══════╤══════╤══════╤══════╤══════╤══════╤═══════╤═════╤═════╕
│   X0 │   X1 │   S0 │   S1 │   S2 │   S3 │ A0    │   P │   P │
╞══════╪══════╪══════╪══════╪══════╪══════╪═══════╪═════╪═════╡
│    1 │    0 │    1 │   -1 │    0 │    0 │ 0.0   │   0 │ 375 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    2 │    0 │    1 │ -1.0  │   0 │ 300 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │   -4 │    1 │    0 │ 0.0   │   0 │ 100 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    1 │    0 │    1 │    0 │    0 │ 0.0   │   0 │ 225 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    4 │    0 │    0 │ 1.0*M │  

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │   -4 │    1 │    0 │ 0.0   │   0 │ 100 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    1 │    0 │    1 │    0 │    0 │ 0.0   │   0 │ 225 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    4 │    0 │    0 │ 1.0*M │   1 │ 900 │
╘══════╧══════╧══════╧══════╧══════╧══════╧═══════╧═════╧═════╛
╒══════╤══════╤══════╤══════╤══════╤══════╤═══════╤═════╤═════╕
│   X0 │   X1 │   S0 │   S1 │   S2 │   S3 │ A0    │   P │   P │
╞══════╪══════╪══════╪══════╪══════╪══════╪═══════╪═════╪═════╡
│    1 │    0 │    1 │   -1 │    0 │    0 │ 0.0   │   0 │ 375 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │    2 │    0 │    1 │ -1.0  │   0 │ 300 │
├──────┼──────┼──────┼──────┼──────┼──────┼───────┼─────┼─────┤
│    1 │    0 │    0 │   -4 │    1 │    0 │ 0.0   │  

In [ ]:
if choice == 'MIN':
    while (noSol == True):
      
      table = replaceM(table)
      print(tabulate(table, headers, tablefmt="fancy_grid"))
      # Utiliza la funcion getMin()
      # Esta retorna el valor mas pequeño en la ultima fila de la tabla y su posicion
      minNegative, location = getMax(table)
      # verifica que el minimo sea menor a cero, si no es se termina el while pues ya se tiene la tabla con los resultados
      if minNegative <= 0:
        noSol = False
        break
      
      # Utulizando la posicion del minimo se seleccion la columna pivote
      pivotColumn = table[:, location]
      # Se selecciona la ultima columna de la tabla 
      lastCol = table[:, -1]
      values = []
      # Se recorre este for el numero de restricciones que existen y
      # se divide cada valor de la ultima columna por cada valor de la columna pivote y se guarda en un arreglo
      for x in range (0, numConstraints):
        if pivotColumn[x] != 0:
          val = lastCol[x]/pivotColumn[x]
          values.append(val)
        else: 
          values.append(-1)
     
      # Devuelve el valor mas pequeño de la lista de respuestas
      min, ogVals = getPositiveMin(values)

      # Devuelve la posicion en donde se encuentra el minimo para luego utilizarlo para encontrar el pivot
      pivLoc = ogVals.index(min)
      pivot = pivotColumn[pivLoc]

      print(f"\nEl numero pivote es: {pivot}")

      # Con la misma posicion de antes vamos a traer la fila pivote
      pivotRow = np.array(table[pivLoc], dtype=float)
      # Se recorre la fila pivote y se divide cada valor por el pivote
      for i in range(len(pivotRow)):
        val = pivotRow[i]/pivot
        pivotRow[i] = val
      # Se remplaza la fila pivote modificada en la tabla
      table[pivLoc] = pivotRow
      printTable(table)
      numRows = len(table)
      
      # Se recorre cada fila
      for x in range(0, numRows):
        # Si la posicion del pivote es igual a la posicion que toca en la iteracion y se salta la fila
        if pivLoc == x:
          continue
        else:
          # Se trae la fila que se va a modifica
          row = np.array(table[x])
          # Es el coeficiente que va a afectar los valores de la fila pivote
          coef = pivotColumn[x]
          # Este for recorre los elementos de la fila que se esta modificando
          for i in range(len(row)):
            # Se hace la operacion con el coeficiente a cada elemento de la fila
            # para hacer cero los valores arriba del pivote
            newVal = row[i] - coef*pivotRow[i]
            row[i] = newVal
          # Se inserta la fila modificada en la tabla
          table[x] = row

      print("TABLA FINAL DE RESULTADOS")
      print(tabulate(table, headers, tablefmt="fancy_grid"))

In [ ]:
# Se crea una lista para almacenar los resultados
result = []

# Agarra la ultima columna de la tabla 
lastColumn = table[:,-1]
# Recorre de 0 a el numero de variables ingresadas en el modelo
for x in range(numVars):
  col = table[:,x] # Agarra cada columna de las variables de la tabla
  if 1 in col and 0 in col: # Verifica si el 1 y el 0 estan en la columna
    for index in range(len(col)): # Rocorre de 0 a el largo de la columna 
      if (col[index] == 1): # Mira si existe un uno en alguna de las posiciones 
        result.append(lastColumn[index]) #Si si hay un 1 agarra la posicion en donde esta el 1 y 
        #esa misma posicion la busca en la ultima columna de resultados y ese valor lo agrega en el arreglo de resultados
  else: # Si no hay 1s ni 0s 
      result.append(0) # Agrega un cero al arreglo de resultados pq el valor de la variable es 0
result.append(lastColumn[-1]) # Agrega el ultimo valor de la ultima columna ya que ese es el resultado optimo

# Imprime los resultados
x = 'x'
print("Resultado optimo: ")
for i in range(0, numVars):
  print(f"{x}{i} = {result[i]}")
print(f"z = {result[-1]}")